In [2]:
import pandas
dd = pandas.read_csv(r'C:\Users\Access\Downloads\eurusd_.csv')


In [3]:
dd

Gmt time     Open     High      Low    Close  \
0        2024-04-01 00:01:39.471  1.07944  1.07944  1.07944  1.07944   
1        2024-04-01 00:01:40.638  1.07944  1.07944  1.07944  1.07944   
2        2024-04-01 00:01:40.794  1.07944  1.07944  1.07944  1.07944   
3        2024-04-01 00:01:41.199  1.07944  1.07944  1.07944  1.07944   
4        2024-04-01 00:01:42.768  1.07944  1.07944  1.07944  1.07944   
...                          ...      ...      ...      ...      ...   
9059327  2024-09-27 20:59:58.689  1.11628  1.11628  1.11628  1.11628   
9059328  2024-09-27 20:59:58.740  1.11617  1.11617  1.11617  1.11617   
9059329  2024-09-27 20:59:58.941  1.11614  1.11614  1.11614  1.11614   
9059330  2024-09-27 20:59:59.094  1.11619  1.11619  1.11619  1.11619   
9059331  2024-09-27 20:59:59.145  1.11619  1.11619  1.11619  1.11619   

               Volume   EMA_100    EMA_50    EMA_21    EMA_13     EMA_7  \
0        9.000000e+05  1.079285  1.079343  1.079391  1.079412  1.079429   
1        9.000000e+05  1.079288  1.079347  1.079396  1.079416  1.079432   
2        9.000000e+05  1.079291  1.079350  1.079400  1.079419  1.079434   
3        9.000000e+05  1.079294  1.079354  1.079403  1.079422  1.079435   
4        9.000000e+05  1.079297  1.079357  1.079407  1.079425  1.079437   
...               ...       ...       ...       ...       ...       ...   
9059327  1.800000e+06  1.116314  1.116306  1.116292  1.116284  1.116277   
9059328  4.500000e+06  1.116312  1.116301  1.116281  1.116268  1.116250   
9059329  9.000000e+05  1.116308  1.116295  1.116268  1.116250  1.116223   
9059330  1.800000e+06  1.116306  1.116291  1.116261  1.116241  1.116215   
9059331  1.800000e+06  1.116304  1.116287  1.116255  1.116234  1.116208   

            RSI_10    ATR_10    ATR_30  
0        91.912193  0.000006  0.000008  
1        91.912193  0.000005  0.000007  
2        91.912193  0.000005  0.000007  
3        91.912193  0.000004  0.000007  
4        91.912193  0.000004  0.000007  
...            ...       ...       ...  
9059327  46.989565  0.000020  0.000022  
9059328  28.959480  0.000029  0.000025  
9059329  25.942987  0.000029  0.000025  
9059330  37.918175  0.000031  0.000026  
9059331  37.918175  0.000028  0.000025  

[9059332 rows x 14 columns]

In [5]:
import pandas as pd



data = dd
tp = 0.00006
sl = 0.00003

# إنشاء عمود لتحديد نوع الصفقة بناءً على تقاطع EMA_13 و EMA_21
data['Signal'] = 0
data['Signal'] = data.apply(lambda row: 1 if row['EMA_13'] > row['EMA_21'] else -1 if row['EMA_13'] < row['EMA_21'] else 0, axis=1)

# تحديد الصفوف التي يحدث فيها تقاطع (عندما يتغير الاتجاه)
data['Crossover'] = data['Signal'].diff().fillna(0)

# إنشاء أعمدة فارغة للإشارة وهدف السعر ووقف الخسارة
data['Trade Type'] = None
data['Take Profit'] = None
data['Stop Loss'] = None

# حساب هدف السعر ووقف الخسارة فقط عند حدوث التقاطع
for i in range(len(data)):
    if data.loc[i, 'Crossover'] == 2:  # تقاطع صعودي (شراء)
        data.loc[i, 'Trade Type'] = 'Buy'
        data.loc[i, 'Take Profit'] = data.loc[i, 'Open'] + tp
        data.loc[i, 'Stop Loss'] = data.loc[i, 'Open'] - sl
    elif data.loc[i, 'Crossover'] == -2:  # تقاطع هبوطي (بيع)
        data.loc[i, 'Trade Type'] = 'Sell'
        data.loc[i, 'Take Profit'] = data.loc[i, 'Open'] - tp
        data.loc[i, 'Stop Loss'] = data.loc[i, 'Open'] + sl

# حذف الصفوف التي لا تحتوي على صفقة أو كانت الصفقة خاسرة
filtered_trades = data.dropna(subset=['Trade Type'])

# إضافة عمود لتحديد إذا كانت الصفقة رابحة أو خاسرة
filtered_trades.loc[:, 'Is Winning Trade'] = filtered_trades.apply(
    lambda row: True if (row['Trade Type'] == 'Buy' and row['High'] >= row['Take Profit'] and row['Low'] > row['Stop Loss']) or
                    (row['Trade Type'] == 'Sell' and row['Low'] <= row['Take Profit'] and row['High'] < row['Stop Loss']) else False,
    axis=1
)

# الاحتفاظ بالصفقات الرابحة فقط
winning_trades = filtered_trades[filtered_trades['Is Winning Trade']]



print("تمت إضافة الصفقات الرابحة فقط وحفظها في ملف winning_trades.csv.")


تمت إضافة الصفقات الرابحة فقط وحفظها في ملف winning_trades.csv.


C:\Users\Access\AppData\Local\Temp\ipykernel_15116\2637799659.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  filtered_trades.loc[:, 'Is Winning Trade'] = filtered_trades.apply(


In [6]:
winning_trades

Empty DataFrame
Columns: [Gmt time, Open, High, Low, Close, Volume, EMA_100, EMA_50, EMA_21, EMA_13, EMA_7, RSI_10, ATR_10, ATR_30, Signal, Crossover, Trade Type, Take Profit, Stop Loss, Is Winning Trade]
Index: []

In [8]:
import pandas as pd

# افتراض أن البيانات تم تحميلها في 'dd' DataFrame
data = dd.copy()  # تأكد من العمل على نسخة من البيانات الأصلية

# قيم هدف السعر ووقف الخسارة
tp = 0.00006  # 6 نقاط
sl = 0.00003  # 3 نقاط

# إنشاء عمود لتحديد نوع الصفقة بناءً على تقاطع EMA_13 و EMA_21
data['Signal'] = 0
data['Signal'] = data.apply(lambda row: 1 if row['EMA_13'] > row['EMA_21'] else -1 if row['EMA_13'] < row['EMA_21'] else 0, axis=1)

# تحديد الصفوف التي يحدث فيها تقاطع (عندما يتغير الاتجاه)
data['Crossover'] = data['Signal'].diff().fillna(0)

# إنشاء أعمدة فارغة للإشارة وهدف السعر ووقف الخسارة
data['Trade Type'] = None
data['Take Profit'] = None
data['Stop Loss'] = None

# حساب هدف السعر ووقف الخسارة فقط عند حدوث التقاطع
for i in range(len(data)):
    if data.loc[i, 'Crossover'] == 2:  # تقاطع صعودي (شراء)
        data.loc[i, 'Trade Type'] = 'Buy'
        data.loc[i, 'Take Profit'] = data.loc[i, 'Open'] + tp
        data.loc[i, 'Stop Loss'] = data.loc[i, 'Open'] - sl
    elif data.loc[i, 'Crossover'] == -2:  # تقاطع هبوطي (بيع)
        data.loc[i, 'Trade Type'] = 'Sell'
        data.loc[i, 'Take Profit'] = data.loc[i, 'Open'] - tp
        data.loc[i, 'Stop Loss'] = data.loc[i, 'Open'] + sl

# حذف الصفوف التي لا تحتوي على صفقات
filtered_trades = data.dropna(subset=['Trade Type']).copy()

# إضافة عمود لتحديد إذا كانت الصفقة رابحة أو خاسرة
filtered_trades['Is Winning Trade'] = filtered_trades.apply(
    lambda row: True if (row['Trade Type'] == 'Buy' and row['High'] >= row['Take Profit'] and row['Low'] > row['Stop Loss']) or
                    (row['Trade Type'] == 'Sell' and row['Low'] <= row['Take Profit'] and row['High'] < row['Stop Loss']) else False,
    axis=1
)

# الاحتفاظ بالصفقات الرابحة فقط
winning_trades = filtered_trades[filtered_trades['Is Winning Trade']]

# عرض النتائج
print(winning_trades[['Gmt time', 'Open', 'Trade Type', 'Take Profit', 'Stop Loss']])
print("تمت إضافة الصفقات الرابحة فقط.")


Empty DataFrame
Columns: [Gmt time, Open, Trade Type, Take Profit, Stop Loss]
Index: []
تمت إضافة الصفقات الرابحة فقط.


In [9]:
winning_trades

Empty DataFrame
Columns: [Gmt time, Open, High, Low, Close, Volume, EMA_100, EMA_50, EMA_21, EMA_13, EMA_7, RSI_10, ATR_10, ATR_30, Signal, Crossover, Trade Type, Take Profit, Stop Loss, Is Winning Trade]
Index: []

In [15]:
filtered_trades[60:120]

Gmt time     Open     High      Low    Close  \
1740  2024-04-01 00:50:39.375  1.07956  1.07956  1.07956  1.07956   
1775  2024-04-01 00:51:33.051  1.07955  1.07955  1.07955  1.07955   
1781  2024-04-01 00:51:47.826  1.07952  1.07952  1.07952  1.07952   
1795  2024-04-01 00:52:17.406  1.07955  1.07955  1.07955  1.07955   
1832  2024-04-01 00:53:09.756  1.07959  1.07959  1.07959  1.07959   
1914  2024-04-01 00:55:02.964  1.07938  1.07938  1.07938  1.07938   
1936  2024-04-01 00:55:33.408  1.07935  1.07935  1.07935  1.07935   
1992  2024-04-01 00:56:42.777  1.07923  1.07923  1.07923  1.07923   
1997  2024-04-01 00:56:46.923  1.07919  1.07919  1.07919  1.07919   
2070  2024-04-01 00:59:17.349  1.07905  1.07905  1.07905  1.07905   
2120  2024-04-01 01:00:19.644  1.07909  1.07909  1.07909  1.07909   
2132  2024-04-01 01:00:32.796  1.07915  1.07915  1.07915  1.07915   
2133  2024-04-01 01:00:37.818  1.07913  1.07913  1.07913  1.07913   
2151  2024-04-01 01:01:18.492  1.07914  1.07914  1.07914  1.07914   
2165  2024-04-01 01:01:33.939  1.07911  1.07911  1.07911  1.07911   
2199  2024-04-01 01:02:03.477  1.07905  1.07905  1.07905  1.07905   
2333  2024-04-01 01:06:01.458  1.07935  1.07935  1.07935  1.07935   
2335  2024-04-01 01:06:03.996  1.07937  1.07937  1.07937  1.07937   
2388  2024-04-01 01:07:12.054  1.07941  1.07941  1.07941  1.07941   
2448  2024-04-01 01:09:44.298  1.07926  1.07926  1.07926  1.07926   
2459  2024-04-01 01:09:51.708  1.07922  1.07922  1.07922  1.07922   
2480  2024-04-01 01:10:26.946  1.07924  1.07924  1.07924  1.07924   
2589  2024-04-01 01:13:03.084  1.07940  1.07940  1.07940  1.07940   
2598  2024-04-01 01:13:09.954  1.07942  1.07942  1.07942  1.07942   
2607  2024-04-01 01:13:20.475  1.07938  1.07938  1.07938  1.07938   
2642  2024-04-01 01:14:22.638  1.07937  1.07937  1.07937  1.07937   
2658  2024-04-01 01:14:47.901  1.07932  1.07932  1.07932  1.07932   
2677  2024-04-01 01:15:24.591  1.07936  1.07936  1.07936  1.07936   
2718  2024-04-01 01:16:17.202  1.07937  1.07937  1.07937  1.07937   
2750  2024-04-01 01:17:07.551  1.07935  1.07935  1.07935  1.07935   
2754  2024-04-01 01:17:20.184  1.07931  1.07931  1.07931  1.07931   
2777  2024-04-01 01:17:57.111  1.07931  1.07931  1.07931  1.07931   
2780  2024-04-01 01:18:01.311  1.07930  1.07930  1.07930  1.07930   
2808  2024-04-01 01:18:38.574  1.07930  1.07930  1.07930  1.07930   
2860  2024-04-01 01:19:40.509  1.07934  1.07934  1.07934  1.07934   
2929  2024-04-01 01:21:10.836  1.07925  1.07925  1.07925  1.07925   
2995  2024-04-01 01:22:54.507  1.07928  1.07928  1.07928  1.07928   
3002  2024-04-01 01:23:34.818  1.07930  1.07930  1.07930  1.07930   
3030  2024-04-01 01:25:30.261  1.07927  1.07927  1.07927  1.07927   
3080  2024-04-01 01:27:15.753  1.07919  1.07919  1.07919  1.07919   
3116  2024-04-01 01:28:23.568  1.07919  1.07919  1.07919  1.07919   
3155  2024-04-01 01:29:39.432  1.07921  1.07921  1.07921  1.07921   
3195  2024-04-01 01:30:52.215  1.07922  1.07922  1.07922  1.07922   
3215  2024-04-01 01:32:01.608  1.07925  1.07925  1.07925  1.07925   
3222  2024-04-01 01:32:36.567  1.07922  1.07922  1.07922  1.07922   
3228  2024-04-01 01:32:51.975  1.07925  1.07925  1.07925  1.07925   
3234  2024-04-01 01:33:08.277  1.07922  1.07922  1.07922  1.07922   
3284  2024-04-01 01:34:11.874  1.07918  1.07918  1.07918  1.07918   
3320  2024-04-01 01:35:21.435  1.07917  1.07917  1.07917  1.07917   
3391  2024-04-01 01:37:31.539  1.07900  1.07900  1.07900  1.07900   
3453  2024-04-01 01:40:26.628  1.07906  1.07906  1.07906  1.07906   
3455  2024-04-01 01:40:27.186  1.07909  1.07909  1.07909  1.07909   
3469  2024-04-01 01:40:52.143  1.07906  1.07906  1.07906  1.07906   
3485  2024-04-01 01:41:00.414  1.07910  1.07910  1.07910  1.07910   
3507  2024-04-01 01:41:35.223  1.07909  1.07909  1.07909  1.07909   
3518  2024-04-01 01:41:56.235  1.07912  1.07912  1.07912  1.07912   
3541  2024-04-01 01:42:07.035  1.07910  1.07910  1.07910  1.07910   
3550  2024-04-01 01

In [12]:
data_cleaned = filtered_trades[filtered_trades['Is Winning Trade'] != False]


In [13]:
data_cleaned

Empty DataFrame
Columns: [Gmt time, Open, High, Low, Close, Volume, EMA_100, EMA_50, EMA_21, EMA_13, EMA_7, RSI_10, ATR_10, ATR_30, Signal, Crossover, Trade Type, Take Profit, Stop Loss, Is Winning Trade]
Index: []

In [16]:
dd

Gmt time     Open     High      Low    Close  \
0        2024-04-01 00:01:39.471  1.07944  1.07944  1.07944  1.07944   
1        2024-04-01 00:01:40.638  1.07944  1.07944  1.07944  1.07944   
2        2024-04-01 00:01:40.794  1.07944  1.07944  1.07944  1.07944   
3        2024-04-01 00:01:41.199  1.07944  1.07944  1.07944  1.07944   
4        2024-04-01 00:01:42.768  1.07944  1.07944  1.07944  1.07944   
...                          ...      ...      ...      ...      ...   
9059327  2024-09-27 20:59:58.689  1.11628  1.11628  1.11628  1.11628   
9059328  2024-09-27 20:59:58.740  1.11617  1.11617  1.11617  1.11617   
9059329  2024-09-27 20:59:58.941  1.11614  1.11614  1.11614  1.11614   
9059330  2024-09-27 20:59:59.094  1.11619  1.11619  1.11619  1.11619   
9059331  2024-09-27 20:59:59.145  1.11619  1.11619  1.11619  1.11619   

               Volume   EMA_100    EMA_50    EMA_21    EMA_13     EMA_7  \
0        9.000000e+05  1.079285  1.079343  1.079391  1.079412  1.079429   
1        9.000000e+05  1.079288  1.079347  1.079396  1.079416  1.079432   
2        9.000000e+05  1.079291  1.079350  1.079400  1.079419  1.079434   
3        9.000000e+05  1.079294  1.079354  1.079403  1.079422  1.079435   
4        9.000000e+05  1.079297  1.079357  1.079407  1.079425  1.079437   
...               ...       ...       ...       ...       ...       ...   
9059327  1.800000e+06  1.116314  1.116306  1.116292  1.116284  1.116277   
9059328  4.500000e+06  1.116312  1.116301  1.116281  1.116268  1.116250   
9059329  9.000000e+05  1.116308  1.116295  1.116268  1.116250  1.116223   
9059330  1.800000e+06  1.116306  1.116291  1.116261  1.116241  1.116215   
9059331  1.800000e+06  1.116304  1.116287  1.116255  1.116234  1.116208   

            RSI_10    ATR_10    ATR_30  Signal  Crossover Trade Type  \
0        91.912193  0.000006  0.000008       1        0.0       None   
1        91.912193  0.000005  0.000007       1        0.0       None   
2        91.912193  0.000005  0.000007       1        0.0       None   
3        91.912193  0.000004  0.000007       1        0.0       None   
4        91.912193  0.000004  0.000007       1        0.0       None   
...            ...       ...       ...     ...        ...        ...   
9059327  46.989565  0.000020  0.000022      -1        0.0       None   
9059328  28.959480  0.000029  0.000025      -1        0.0       None   
9059329  25.942987  0.000029  0.000025      -1        0.0       None   
9059330  37.918175  0.000031  0.000026      -1        0.0       None   
9059331  37.918175  0.000028  0.000025      -1        0.0       None   

        Take Profit Stop Loss  
0              None      None  
1              None      None  
2              None      None  
3              None      None  
4              None      None  
...             ...       ...  
9059327        None      None  
9059328        None      None  
9059329        None      None  
9059330        None      None  
9059331        None      None  

[9059332 rows x 19 columns]

In [17]:
import pandas as pd

# افتراض أن البيانات تم تحميلها في 'dd' DataFrame
data = dd.copy()  # تأكد من العمل على نسخة من البيانات الأصلية

# قيم هدف السعر ووقف الخسارة
tp = 0.00006  # 6 نقاط
sl = 0.00003  # 3 نقاط

# إنشاء عمود لتحديد نوع الصفقة بناءً على تقاطع EMA_13 و EMA_21
data['Signal'] = 0
data['Signal'] = data.apply(lambda row: 1 if row['EMA_13'] > row['EMA_21'] else -1 if row['EMA_13'] < row['EMA_21'] else 0, axis=1)

# تحديد الصفوف التي يحدث فيها تقاطع (عندما يتغير الاتجاه)
data['Crossover'] = data['Signal'].diff().fillna(0)

# إنشاء أعمدة فارغة للإشارة وهدف السعر ووقف الخسارة
data['Trade Type'] = None
data['Take Profit'] = None
data['Stop Loss'] = None

# حساب هدف السعر ووقف الخسارة فقط عند حدوث التقاطع
for i in range(len(data)):
    if data.loc[i, 'Crossover'] == 2:  # تقاطع صعودي (شراء)
        data.loc[i, 'Trade Type'] = 'Buy'
        data.loc[i, 'Take Profit'] = data.loc[i, 'Open'] + tp
        data.loc[i, 'Stop Loss'] = data.loc[i, 'Open'] - sl
    elif data.loc[i, 'Crossover'] == -2:  # تقاطع هبوطي (بيع)
        data.loc[i, 'Trade Type'] = 'Sell'
        data.loc[i, 'Take Profit'] = data.loc[i, 'Open'] - tp
        data.loc[i, 'Stop Loss'] = data.loc[i, 'Open'] + sl

# حذف الصفوف التي لا تحتوي على صفقات
filtered_trades = data.dropna(subset=['Trade Type']).copy()

# إضافة عمود لتحديد إذا كانت الصفقة رابحة أو خاسرة
def is_winning_trade(row):
    if row['Trade Type'] == 'Buy':
        if row['Low'] <= row['Stop Loss']:  # تم الوصول إلى وقف الخسارة أولاً
            return False
        elif row['High'] >= row['Take Profit']:  # تم الوصول إلى هدف الربح
            return True
    elif row['Trade Type'] == 'Sell':
        if row['High'] >= row['Stop Loss']:  # تم الوصول إلى وقف الخسارة أولاً
            return False
        elif row['Low'] <= row['Take Profit']:  # تم الوصول إلى هدف الربح
            return True
    return False

# تطبيق الدالة لتحديد الصفقات الرابحة
filtered_trades['Is Winning Trade'] = filtered_trades.apply(is_winning_trade, axis=1)

# الاحتفاظ بالصفقات الرابحة فقط
winning_trades = filtered_trades[filtered_trades['Is Winning Trade']]

# عرض النتائج
print("تمت إضافة الصفقات الرابحة فقط.")


تمت إضافة الصفقات الرابحة فقط.


In [18]:
winning_trades

Empty DataFrame
Columns: [Gmt time, Open, High, Low, Close, Volume, EMA_100, EMA_50, EMA_21, EMA_13, EMA_7, RSI_10, ATR_10, ATR_30, Signal, Crossover, Trade Type, Take Profit, Stop Loss, Is Winning Trade]
Index: []

In [19]:
filtered_trades


Gmt time     Open     High      Low    Close  \
16       2024-04-01 00:01:50.784  1.07938  1.07938  1.07938  1.07938   
62       2024-04-01 00:02:42.405  1.07934  1.07934  1.07934  1.07934   
125      2024-04-01 00:04:00.852  1.07945  1.07945  1.07945  1.07945   
132      2024-04-01 00:04:30.708  1.07949  1.07949  1.07949  1.07949   
133      2024-04-01 00:04:30.762  1.07947  1.07947  1.07947  1.07947   
...                          ...      ...      ...      ...      ...   
9059308  2024-09-27 20:59:55.095  1.11631  1.11631  1.11631  1.11631   
9059311  2024-09-27 20:59:55.350  1.11634  1.11634  1.11634  1.11634   
9059312  2024-09-27 20:59:55.404  1.11631  1.11631  1.11631  1.11631   
9059314  2024-09-27 20:59:55.704  1.11634  1.11634  1.11634  1.11634   
9059317  2024-09-27 20:59:56.160  1.11626  1.11626  1.11626  1.11626   

               Volume   EMA_100    EMA_50    EMA_21    EMA_13     EMA_7  \
16       9.000000e+05  1.079319  1.079372  1.079399  1.079398  1.079391   
62       1.800000e+06  1.079322  1.079330  1.079322  1.079322  1.079327   
125      9.000000e+05  1.079417  1.079459  1.079487  1.079486  1.079477   
132      9.000000e+05  1.079425  1.079464  1.079485  1.079485  1.079485   
133      9.000000e+05  1.079426  1.079464  1.079483  1.079483  1.079481   
...               ...       ...       ...       ...       ...       ...   
9059308  9.000000e+05  1.116324  1.116322  1.116322  1.116321  1.116320   
9059311  9.000000e+05  1.116324  1.116323  1.116323  1.116323  1.116325   
9059312  9.000000e+05  1.116324  1.116322  1.116322  1.116321  1.116321   
9059314  9.000000e+05  1.116324  1.116323  1.116323  1.116324  1.116326   
9059317  9.000000e+05  1.116323  1.116321  1.116318  1.116315  1.116308   

            RSI_10    ATR_10    ATR_30  Signal  Crossover Trade Type  \
16       29.886993  0.000005  0.000007      -1       -2.0       Sell   
62       68.667825  0.000005  0.000005       1        2.0        Buy   
125      30.202891  0.000010  0.000009      -1       -2.0       Sell   
132      52.992617  0.000009  0.000009       1        2.0        Buy   
133      42.814611  0.000010  0.000010      -1       -2.0       Sell   
...            ...       ...       ...     ...        ...        ...   
9059308  48.059856  0.000033  0.000025      -1       -2.0       Sell   
9059311  53.106030  0.000030  0.000025       1        2.0        Buy   
9059312  47.860002  0.000030  0.000025      -1       -2.0       Sell   
9059314  53.358578  0.000027  0.000024       1        2.0        Buy   
9059317  38.551098  0.000028  0.000025      -1       -2.0       Sell   

        Take Profit Stop Loss  Is Winning Trade  
16          1.07932   1.07941             False  
62           1.0794   1.07931             False  
125         1.07939   1.07948             False  
132         1.07955   1.07946             False  
133         1.07941    1.0795             False  
...             ...       ...               ...  
9059308     1.11625   1.11634             False  
9059311      1.1164   1.11631             False  
9059312     1.11625   1.11634             False  
9059314      1.1164   1.11631             False  
9059317      1.1162   1.11629             False  

[346215 rows x 20 columns]

In [21]:
import pandas as pd

# افتراض أن البيانات تم تحميلها في 'dd' DataFrame
data = dd.copy()  # تأكد من العمل على نسخة من البيانات الأصلية

# قيم هدف السعر ووقف الخسارة
tp = 0.00006  # 6 نقاط
sl = 0.00003  # 3 نقاط

# إنشاء عمود لتحديد نوع الصفقة بناءً على تقاطع EMA_13 و EMA_21
data['Signal'] = 0
data['Signal'] = data.apply(lambda row: 1 if row['EMA_13'] > row['EMA_21'] else -1 if row['EMA_13'] < row['EMA_21'] else 0, axis=1)

# تحديد الصفوف التي يحدث فيها تقاطع (عندما يتغير الاتجاه)
data['Crossover'] = data['Signal'].diff().fillna(0)

# إنشاء أعمدة فارغة للإشارة وهدف السعر ووقف الخسارة
data['Trade Type'] = None
data['Take Profit'] = None
data['Stop Loss'] = None

# حساب هدف السعر ووقف الخسارة فقط عند حدوث التقاطع
for i in range(len(data)):
    if data.loc[i, 'Crossover'] == 2:  # تقاطع صعودي (شراء)
        data.loc[i, 'Trade Type'] = 'Buy'
        data.loc[i, 'Take Profit'] = data.loc[i, 'Open'] + tp
        data.loc[i, 'Stop Loss'] = data.loc[i, 'Open'] - sl
    elif data.loc[i, 'Crossover'] == -2:  # تقاطع هبوطي (بيع)
        data.loc[i, 'Trade Type'] = 'Sell'
        data.loc[i, 'Take Profit'] = data.loc[i, 'Open'] - tp
        data.loc[i, 'Stop Loss'] = data.loc[i, 'Open'] + sl

# حذف الصفوف التي لا تحتوي على صفقات
filtered_trades = data.dropna(subset=['Trade Type']).copy()

# إضافة عمود لتحديد إذا كانت الصفقة رابحة أو خاسرة
def is_winning_trade(row):
    if row['Trade Type'] == 'Buy':
        # تحقق من حالة الشراء
        if row['Low'] <= row['Stop Loss']:
            print(f"خسارة في الصف {row.name}: السعر انخفض ووصل إلى وقف الخسارة")
            return False
        elif row['High'] >= row['Take Profit']:
            print(f"ربح في الصف {row.name}: السعر ارتفع ووصل إلى هدف الربح")
            return True
    elif row['Trade Type'] == 'Sell':
        # تحقق من حالة البيع
        if row['High'] >= row['Stop Loss']:
            print(f"خسارة في الصف {row.name}: السعر ارتفع ووصل إلى وقف الخسارة")
            return False
        elif row['Low'] <= row['Take Profit']:
            print(f"ربح في الصف {row.name}: السعر انخفض ووصل إلى هدف الربح")
            return True
    print(f"الصف {row.name} لم يحقق ربح أو خسارة")  # إذا لم يتحقق أي منهما
    return False

# تطبيق الدالة لتحديد الصفقات الرابحة
filtered_trades['Is Winning Trade'] = filtered_trades.apply(is_winning_trade, axis=1)

# الاحتفاظ بالصفقات الرابحة فقط
winning_trades = filtered_trades[filtered_trades['Is Winning Trade']]

# عرض النتائج
print("تمت إضافة الصفقات الرابحة فقط.")


الصف 16 لم يحقق ربح أو خسارة
الصف 62 لم يحقق ربح أو خسارة
الصف 125 لم يحقق ربح أو خسارة
الصف 132 لم يحقق ربح أو خسارة
الصف 133 لم يحقق ربح أو خسارة
الصف 150 لم يحقق ربح أو خسارة
الصف 178 لم يحقق ربح أو خسارة
الصف 191 لم يحقق ربح أو خسارة
الصف 200 لم يحقق ربح أو خسارة
الصف 213 لم يحقق ربح أو خسارة
الصف 236 لم يحقق ربح أو خسارة
الصف 263 لم يحقق ربح أو خسارة
الصف 286 لم يحقق ربح أو خسارة
الصف 334 لم يحقق ربح أو خسارة
الصف 342 لم يحقق ربح أو خسارة
الصف 363 لم يحقق ربح أو خسارة
الصف 392 لم يحقق ربح أو خسارة
الصف 439 لم يحقق ربح أو خسارة
الصف 486 لم يحقق ربح أو خسارة
الصف 507 لم يحقق ربح أو خسارة
الصف 513 لم يحقق ربح أو خسارة
الصف 539 لم يحقق ربح أو خسارة
الصف 540 لم يحقق ربح أو خسارة
الصف 559 لم يحقق ربح أو خسارة
الصف 591 لم يحقق ربح أو خسارة
الصف 610 لم يحقق ربح أو خسارة
الصف 653 لم يحقق ربح أو خسارة
الصف 689 لم يحقق ربح أو خسارة
الصف 738 لم يحقق ربح أو خسارة
الصف 772 لم يحقق ربح أو خسارة
الصف 774 لم يحقق ربح أو خسارة
الصف 787 لم يحقق ربح أو خسارة
الصف 823 لم يحقق ربح أو خسارة
الصف 827 لم 

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)




الصف 4603769 لم يحقق ربح أو خسارة
الصف 4603811 لم يحقق ربح أو خسارة
الصف 4603815 لم يحقق ربح أو خسارة
الصف 4603862 لم يحقق ربح أو خسارة
الصف 4603889 لم يحقق ربح أو خسارة
الصف 4603911 لم يحقق ربح أو خسارة
الصف 4603932 لم يحقق ربح أو خسارة
الصف 4603933 لم يحقق ربح أو خسارة
الصف 4603934 لم يحقق ربح أو خسارة
الصف 4603935 لم يحقق ربح أو خسارة
الصف 4603941 لم يحقق ربح أو خسارة
الصف 4603947 لم يحقق ربح أو خسارة
الصف 4603951 لم يحقق ربح أو خسارة
الصف 4603953 لم يحقق ربح أو خسارة
الصف 4603955 لم يحقق ربح أو خسارة
الصف 4603956 لم يحقق ربح أو خسارة
الصف 4603985 لم يحقق ربح أو خسارة
الصف 4604038 لم يحقق ربح أو خسارة
الصف 4604044 لم يحقق ربح أو خسارة
الصف 4604073 لم يحقق ربح أو خسارة
الصف 4604074 لم يحقق ربح أو خسارة
الصف 4604100 لم يحقق ربح أو خسارة
الصف 4604106 لم يحقق ربح أو خسارة
الصف 4604116 لم يحقق ربح أو خسارة
الصف 4604123 لم يحقق ربح أو خسارة
الصف 4604172 لم يحقق ربح أو خسارة
الصف 4604265 لم يحقق ربح أو خسارة
الصف 4604325 لم يحقق ربح أو خسارة
الصف 4604407 لم يحقق ربح أو خسارة
الصف 4604433 

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



الصف 7003847 لم يحقق ربح أو خسارة
الصف 7003851 لم يحقق ربح أو خسارة
الصف 7004028 لم يحقق ربح أو خسارة
الصف 7004047 لم يحقق ربح أو خسارة
الصف 7004055 لم يحقق ربح أو خسارة
الصف 7004083 لم يحقق ربح أو خسارة
الصف 7004115 لم يحقق ربح أو خسارة
الصف 7004141 لم يحقق ربح أو خسارة
الصف 7004172 لم يحقق ربح أو خسارة
الصف 7004186 لم يحقق ربح أو خسارة
الصف 7004279 لم يحقق ربح أو خسارة
الصف 7004348 لم يحقق ربح أو خسارة
الصف 7004364 لم يحقق ربح أو خسارة
الصف 7004370 لم يحقق ربح أو خسارة
الصف 7004379 لم يحقق ربح أو خسارة
الصف 7004409 لم يحقق ربح أو خسارة
الصف 7004442 لم يحقق ربح أو خسارة
الصف 7004455 لم يحقق ربح أو خسارة
الصف 7004468 لم يحقق ربح أو خسارة
الصف 7004497 لم يحقق ربح أو خسارة
الصف 7004525 لم يحقق ربح أو خسارة
الصف 7004537 لم يحقق ربح أو خسارة
الصف 7004543 لم يحقق ربح أو خسارة
الصف 7004555 لم يحقق ربح أو خسارة
الصف 7004586 لم يحقق ربح أو خسارة
الصف 7004622 لم يحقق ربح أو خسارة
الصف 7004626 لم يحقق ربح أو خسارة
الصف 7004632 لم يحقق ربح أو خسارة
الصف 7004634 لم يحقق ربح أو خسارة
الصف 7004736 ل

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



تمت إضافة الصفقات الرابحة فقط.


In [20]:
dd

Gmt time     Open     High      Low    Close  \
0        2024-04-01 00:01:39.471  1.07944  1.07944  1.07944  1.07944   
1        2024-04-01 00:01:40.638  1.07944  1.07944  1.07944  1.07944   
2        2024-04-01 00:01:40.794  1.07944  1.07944  1.07944  1.07944   
3        2024-04-01 00:01:41.199  1.07944  1.07944  1.07944  1.07944   
4        2024-04-01 00:01:42.768  1.07944  1.07944  1.07944  1.07944   
...                          ...      ...      ...      ...      ...   
9059327  2024-09-27 20:59:58.689  1.11628  1.11628  1.11628  1.11628   
9059328  2024-09-27 20:59:58.740  1.11617  1.11617  1.11617  1.11617   
9059329  2024-09-27 20:59:58.941  1.11614  1.11614  1.11614  1.11614   
9059330  2024-09-27 20:59:59.094  1.11619  1.11619  1.11619  1.11619   
9059331  2024-09-27 20:59:59.145  1.11619  1.11619  1.11619  1.11619   

               Volume   EMA_100    EMA_50    EMA_21    EMA_13     EMA_7  \
0        9.000000e+05  1.079285  1.079343  1.079391  1.079412  1.079429   
1        9.000000e+05  1.079288  1.079347  1.079396  1.079416  1.079432   
2        9.000000e+05  1.079291  1.079350  1.079400  1.079419  1.079434   
3        9.000000e+05  1.079294  1.079354  1.079403  1.079422  1.079435   
4        9.000000e+05  1.079297  1.079357  1.079407  1.079425  1.079437   
...               ...       ...       ...       ...       ...       ...   
9059327  1.800000e+06  1.116314  1.116306  1.116292  1.116284  1.116277   
9059328  4.500000e+06  1.116312  1.116301  1.116281  1.116268  1.116250   
9059329  9.000000e+05  1.116308  1.116295  1.116268  1.116250  1.116223   
9059330  1.800000e+06  1.116306  1.116291  1.116261  1.116241  1.116215   
9059331  1.800000e+06  1.116304  1.116287  1.116255  1.116234  1.116208   

            RSI_10    ATR_10    ATR_30  Signal  Crossover Trade Type  \
0        91.912193  0.000006  0.000008       1        0.0       None   
1        91.912193  0.000005  0.000007       1        0.0       None   
2        91.912193  0.000005  0.000007       1        0.0       None   
3        91.912193  0.000004  0.000007       1        0.0       None   
4        91.912193  0.000004  0.000007       1        0.0       None   
...            ...       ...       ...     ...        ...        ...   
9059327  46.989565  0.000020  0.000022      -1        0.0       None   
9059328  28.959480  0.000029  0.000025      -1        0.0       None   
9059329  25.942987  0.000029  0.000025      -1        0.0       None   
9059330  37.918175  0.000031  0.000026      -1        0.0       None   
9059331  37.918175  0.000028  0.000025      -1        0.0       None   

        Take Profit Stop Loss  
0              None      None  
1              None      None  
2              None      None  
3              None      None  
4              None      None  
...             ...       ...  
9059327        None      None  
9059328        None      None  
9059329        None      None  
9059330        None      None  
9059331        None      None  

[9059332 rows x 19 columns]

In [24]:
import pandas as pd
import numpy as np
df = dd 
# Initialize target price and stop-loss columns
df['Target_Price'] = np.nan
df['Stop_Loss'] = np.nan

# Define stop-loss in pips (e.g., 20 pips) and the RR
stop_loss_pips = 0.00003 # 20 pips converted to price value for major pairs
rr = 1  # risk-reward ratio (1:3)

# Calculate EMA crossovers in a vectorized manner
bullish_crossover = (df['EMA_13'] > df['EMA_21']) & (df['EMA_13'].shift(1) <= df['EMA_21'].shift(1))
bearish_crossover = (df['EMA_13'] < df['EMA_21']) & (df['EMA_13'].shift(1) >= df['EMA_21'].shift(1))

# Create a signal column: +1 for buy, -1 for sell
df['Signal'] = np.where(bullish_crossover, 1, np.where(bearish_crossover, -1, 0))

# Handle buy signals
buy_signals = df[df['Signal'] == 1]
buy_entry_prices = buy_signals['Close']
df.loc[buy_signals.index, 'Stop_Loss'] = buy_entry_prices - stop_loss_pips  # set stop-loss for buys
df.loc[buy_signals.index, 'Target_Price'] = buy_entry_prices + (rr * stop_loss_pips)  # set target for buys

# Handle sell signals
sell_signals = df[df['Signal'] == -1]
sell_entry_prices = sell_signals['Close']
df.loc[sell_signals.index, 'Stop_Loss'] = sell_entry_prices + stop_loss_pips  # set stop-loss for sells
df.loc[sell_signals.index, 'Target_Price'] = sell_entry_prices - (rr * stop_loss_pips)  # set target for sells

# Optimized lookahead to check if target or stop-loss is hit first
for i in range(len(df) - 1):
    # If there's a buy signal
    if df['Signal'].iloc[i] == 1:
        for j in range(i + 1, len(df)):
            if df['High'].iloc[j] >= df['Target_Price'].iloc[i]:  # Target price hit for buy
                df.loc[i, 'Target_Price'] = df['Target_Price'].iloc[i]  # Take profit reached
                break
            elif df['Low'].iloc[j] <= df['Stop_Loss'].iloc[i]:  # Stop-loss hit for buy
                df.loc[i, 'Target_Price'] = np.nan  # Stop-loss hit, target invalidated
                break

    # If there's a sell signal
    elif df['Signal'].iloc[i] == -1:
        for j in range(i + 1, len(df)):
            if df['Low'].iloc[j] <= df['Target_Price'].iloc[i]:  # Target price hit for sell
                df.loc[i, 'Target_Price'] = df['Target_Price'].iloc[i]  # Take profit reached
                break
            elif df['High'].iloc[j] >= df['Stop_Loss'].iloc[i]:  # Stop-loss hit for sell
                df.loc[i, 'Target_Price'] = np.nan  # Stop-loss hit, target invalidated
                break

# Remove intermediate signal column after calculations
#df.drop(columns=['Stop_Loss'], inplace=True)



In [25]:
df

Gmt time     Open     High      Low    Close  \
0        2024-04-01 00:01:39.471  1.07944  1.07944  1.07944  1.07944   
1        2024-04-01 00:01:40.638  1.07944  1.07944  1.07944  1.07944   
2        2024-04-01 00:01:40.794  1.07944  1.07944  1.07944  1.07944   
3        2024-04-01 00:01:41.199  1.07944  1.07944  1.07944  1.07944   
4        2024-04-01 00:01:42.768  1.07944  1.07944  1.07944  1.07944   
...                          ...      ...      ...      ...      ...   
9059327  2024-09-27 20:59:58.689  1.11628  1.11628  1.11628  1.11628   
9059328  2024-09-27 20:59:58.740  1.11617  1.11617  1.11617  1.11617   
9059329  2024-09-27 20:59:58.941  1.11614  1.11614  1.11614  1.11614   
9059330  2024-09-27 20:59:59.094  1.11619  1.11619  1.11619  1.11619   
9059331  2024-09-27 20:59:59.145  1.11619  1.11619  1.11619  1.11619   

               Volume   EMA_100    EMA_50    EMA_21    EMA_13  ...     RSI_10  \
0        9.000000e+05  1.079285  1.079343  1.079391  1.079412  ...  91.912193   
1        9.000000e+05  1.079288  1.079347  1.079396  1.079416  ...  91.912193   
2        9.000000e+05  1.079291  1.079350  1.079400  1.079419  ...  91.912193   
3        9.000000e+05  1.079294  1.079354  1.079403  1.079422  ...  91.912193   
4        9.000000e+05  1.079297  1.079357  1.079407  1.079425  ...  91.912193   
...               ...       ...       ...       ...       ...  ...        ...   
9059327  1.800000e+06  1.116314  1.116306  1.116292  1.116284  ...  46.989565   
9059328  4.500000e+06  1.116312  1.116301  1.116281  1.116268  ...  28.959480   
9059329  9.000000e+05  1.116308  1.116295  1.116268  1.116250  ...  25.942987   
9059330  1.800000e+06  1.116306  1.116291  1.116261  1.116241  ...  37.918175   
9059331  1.800000e+06  1.116304  1.116287  1.116255  1.116234  ...  37.918175   

           ATR_10    ATR_30  Signal  Crossover  Trade Type Take Profit  \
0        0.000006  0.000008       0        0.0        None        None   
1        0.000005  0.000007       0        0.0        None        None   
2        0.000005  0.000007       0        0.0        None        None   
3        0.000004  0.000007       0        0.0        None        None   
4        0.000004  0.000007       0        0.0        None        None   
...           ...       ...     ...        ...         ...         ...   
9059327  0.000020  0.000022       0        0.0        None        None   
9059328  0.000029  0.000025       0        0.0        None        None   
9059329  0.000029  0.000025       0        0.0        None        None   
9059330  0.000031  0.000026       0        0.0        None        None   
9059331  0.000028  0.000025       0        0.0        None        None   

        Stop Loss Target_Price  Stop_Loss  
0            None          NaN        NaN  
1            None          NaN        NaN  
2            None          NaN        NaN  
3            None          NaN        NaN  
4            None          NaN        NaN  
...           ...          ...        ...  
9059327      None          NaN        NaN  
9059328      None          NaN        NaN  
9059329      None          NaN        NaN  
9059330      None          NaN        NaN  
9059331      None          NaN        NaN  

[9059332 rows x 21 columns]

In [27]:
df[:60]

Gmt time     Open     High      Low    Close        Volume  \
0   2024-04-01 00:01:39.471  1.07944  1.07944  1.07944  1.07944  9.000000e+05   
1   2024-04-01 00:01:40.638  1.07944  1.07944  1.07944  1.07944  9.000000e+05   
2   2024-04-01 00:01:40.794  1.07944  1.07944  1.07944  1.07944  9.000000e+05   
3   2024-04-01 00:01:41.199  1.07944  1.07944  1.07944  1.07944  9.000000e+05   
4   2024-04-01 00:01:42.768  1.07944  1.07944  1.07944  1.07944  9.000000e+05   
5   2024-04-01 00:01:43.782  1.07944  1.07944  1.07944  1.07944  9.000000e+05   
6   2024-04-01 00:01:43.887  1.07942  1.07942  1.07942  1.07942  9.000000e+05   
7   2024-04-01 00:01:44.091  1.07942  1.07942  1.07942  1.07942  9.000000e+05   
8   2024-04-01 00:01:45.156  1.07941  1.07941  1.07941  1.07941  9.000000e+05   
9   2024-04-01 00:01:45.258  1.07939  1.07939  1.07939  1.07939  9.000000e+05   
10  2024-04-01 00:01:47.082  1.07938  1.07938  1.07938  1.07938  9.000000e+05   
11  2024-04-01 00:01:47.184  1.07939  1.07939  1.07939  1.07939  9.000000e+05   
12  2024-04-01 00:01:48.351  1.07939  1.07939  1.07939  1.07939  9.000000e+05   
13  2024-04-01 00:01:48.960  1.07939  1.07939  1.07939  1.07939  9.000000e+05   
14  2024-04-01 00:01:49.164  1.07939  1.07939  1.07939  1.07939  9.000000e+05   
15  2024-04-01 00:01:49.266  1.07939  1.07939  1.07939  1.07939  9.000000e+05   
16  2024-04-01 00:01:50.784  1.07938  1.07938  1.07938  1.07938  9.000000e+05   
17  2024-04-01 00:01:53.670  1.07939  1.07939  1.07939  1.07939  9.000000e+05   
18  2024-04-01 00:01:54.180  1.07938  1.07938  1.07938  1.07938  1.800000e+06   
19  2024-04-01 00:01:54.333  1.07937  1.07937  1.07937  1.07937  9.000000e+05   
20  2024-04-01 00:01:54.636  1.07937  1.07937  1.07937  1.07937  9.000000e+05   
21  2024-04-01 00:01:57.009  1.07936  1.07936  1.07936  1.07936  9.000000e+05   
22  2024-04-01 00:01:57.111  1.07934  1.07934  1.07934  1.07934  1.800000e+06   
23  2024-04-01 00:01:57.924  1.07933  1.07933  1.07933  1.07933  9.000000e+05   
24  2024-04-01 00:02:01.626  1.07933  1.07933  1.07933  1.07933  9.000000e+05   
25  2024-04-01 00:02:07.497  1.07933  1.07933  1.07933  1.07933  9.000000e+05   
26  2024-04-01 00:02:09.216  1.07932  1.07932  1.07932  1.07932  9.000000e+05   
27  2024-04-01 00:02:09.471  1.07931  1.07931  1.07931  1.07931  2.250000e+06   
28  2024-04-01 00:02:09.777  1.07931  1.07931  1.07931  1.07931  1.350000e+06   
29  2024-04-01 00:02:09.879  1.07931  1.07931  1.07931  1.07931  1.350000e+06   
30  2024-04-01 00:02:10.386  1.07931  1.07931  1.07931  1.07931  2.250000e+06   
31  2024-04-01 00:02:11.346  1.07931  1.07931  1.07931  1.07931  1.350000e+06   
32  2024-04-01 00:02:13.419  1.07931  1.07931  1.07931  1.07931  9.000000e+05   
33  2024-04-01 00:02:13.521  1.07932  1.07932  1.07932  1.07932  9.000000e+05   
34  2024-04-01 00:02:13.626  1.07933  1.07933  1.07933  1.07933  9.000000e+05   
35  2024-04-01 00:02:28.911  1.07933  1.07933  1.07933  1.07933  9.000000e+05   
36  2024-04-01 00:02:29.115  1.07933  1.07933  1.07933  1.07933  9.000000e+05   
37  2024-04-01 00:02:29.370  1.07934  1.07934  1.07934  1.07934  9.000000e+05   
38  2024-04-01 00:02:29.475  1.07934  1.07934  1.07934  1.07934  9.000000e+05   
39  2024-04-01 00:02:29.628  1.07934  1.07934  1.07934  1.07934  9.000000e+05   
40  2024-04-01 00:02:30.537  1.07934  1.07934  1.07934  1.07934  9.000000e+05   
41  2024-04-01 00:02:30.639  1.07934  1.07934  1.07934  1.07934  9.000000e+05   
42  2024-04-01 00:02:31.350  1.07934  1.07934  1.07934  1.07934  9.000000e+05   
43  2024-04-01 00:02:31.452  1.07933  1.07933  1.07933  1.07933  9.000000e+05   
44  2024-04-01 00:02:31.554  1.07931  1.07931  1.07931  1.07931  9.000000e+05   
45  2024-04-01 00:02:31.860  1.07931  1.07931  1.07931  1.07931  9.000000e+05   
46  2024-04-01 00:02:31.962  1.07931  1.07931  1.07931  1.07931  9.000000e+05   
47  2024-04-01 00:02:32.268  1.07931  1.07931  1.07931  1.07931  9.000000e+05   
48  2024-04-01 00:02:32.421  1.07931  1.07931  1.0

In [1]:
dd

NameError: name 'dd' is not defined